In [1]:
import glob 
import gezi
from gezi import tqdm
import pandas as pd
import dask.dataframe as dd
from plotly.graph_objs import Scatter,Layout
import plotly
import plotly.offline as py
import numpy as np
import plotly.graph_objs as go
from plotly.subplots import make_subplots

#setting offilne
plotly.offline.init_notebook_mode(connected=True)

In [2]:
marks = ['tuwen', 'video']

In [3]:
def deal(df):
    df.hour = df.hour.astype(str)
    df = df.groupby(['abtest', 'hour'], as_index=False).last()
    df = df.sort_values(by=['hour'])
    df = df.drop_duplicates()
    df.hour = pd.to_datetime(df.hour, format='%Y%m%d%H')
    return df

def gen_df(mark):
  root = f'/home/gezi/tmp/rank/data/{mark}_hour_sgsapp_v2/infos/15'  
  dfs_offline = []
  dfs_online = []
  for file in tqdm(glob.glob(f'{root}/*/metrics_offline.csv')):
        df = pd.read_csv(file)
        dfs_offline.append(df)
  for file in tqdm(glob.glob(f'{root}/*/metrics_online.csv')):
        df = pd.read_csv(file)
        dfs_online.append(df)
  df_off = deal(pd.concat(dfs_offline))
  df_off.name = mark + '_off'
  df_off.to_csv(f'{root}/metrics_offline.csv')
  df_on = deal(pd.concat(dfs_online))
  df_on.name = mark + '_on'
  df_on.to_csv(f'{root}/metrics_online.csv')
  return df_off, df_on

In [4]:
df_off_tuwen, df_on_tuwen = gen_df('tuwen')

100%|██████████| 783/783 [00:04<00:00, 167.14it/s]


In [5]:
df_tuwen = pd.concat([df_off_tuwen, df_on_tuwen])

In [6]:
df_off_video, df_on_video = gen_df('video')

100%|██████████| 825/825 [00:06<00:00, 136.60it/s]


In [7]:
df_video = pd.concat([df_off_video, df_on_video])

In [8]:
df_off_tuwen.set_index('hour').groupby(pd.Grouper(freq='D')).mean().head()

abtest  Click/auc  Click/click/time_auc  \
hour                                                        
2019-12-01  45600.000000   0.526705              0.586907   
2019-12-02  16233.333333   0.695965              0.591184   
2019-12-03  16233.333333   0.713702              0.588786   
2019-12-04  16233.333333   0.709032              0.595457   
2019-12-05  16233.333333   0.705225              0.596914   

            Click/click/weighted_time_auc  Click/cold/auc  Click/gold/auc  \
hour                                                                        
2019-12-01                       0.510068        0.526491        0.610571   
2019-12-02                       0.609111        0.770011        0.606504   
2019-12-03                       0.612759        0.786073        0.611235   
2019-12-04                       0.638991        0.774983        0.614556   
2019-12-05                       0.642619        0.794891        0.613653   

            Click/group/auc  Click/group/click/time_auc  \
hour                                                      
2019-12-01         0.519889                    0.565608   
2019-12-02         0.642021                    0.561713   
2019-12-03         0.659020                    0.561064   
2019-12-04         0.654655                    0.571101   
2019-12-05         0.650897                    0.572801   

            Click/group/click/top1_best  Click/group/click/top1_click  ...  \
hour                                                                   ...   
2019-12-01                   114.563215                           1.0  ...   
2019-12-02                   110.345797                           1.0  ...   
2019-12-03                   113.672625                           1.0  ...   
2019-12-04                   115.795496                           1.0  ...   
2019-12-05                   120.681839                           1.0  ...   

            group/weighted_time_auc      loss   ori/auc  pos_ratio  \
hour                                                                 
2019-12-01                 0.677149  4.527964  0.525926   0.146663   
2019-12-02                 0.671717  0.906168  0.697315   0.138232   
2019-12-03                 0.681821  0.679366  0.714014   0.137790   
2019-12-04                 0.681846  0.690319  0.709340   0.150208   
2019-12-05                 0.680514  0.637514  0.707312   0.150824   

            stats/click_ratio  stats/time_per_click  stats/time_per_show  \
hour                                                                       
2019-12-01           0.146663             74.220271            10.894944   
2019-12-02           0.138232             73.365221            10.139736   
2019-12-03           0.137790             74.936155            10.336846   
2019-12-04           0.150208             74.966919            11.269700   
2019-12-05           0.150824             77.295794            11.666342   

            stats/time_per_user  time_auc  weighted_time_auc  
hour                                                          
2019-12-01           172.547803  0.704170           0.531587  
2019-12-02           156.087023  0.704865           0.730511  
2019-12-03           163.980882  0.713192           0.747307  
2019-12-04           180.742498  0.708288           0.747635  
2019-12-05           185.450663  0.704759           0.747112  

[5 rows x 133 columns]

In [9]:
x = df_off_tuwen.groupby([df_off_tuwen['hour'].dt.date])['auc'].mean()

In [10]:
df_off_tuwen.set_index('hour').resample('D')['auc'].mean().head()

hour
2019-12-01    0.526705
2019-12-02    0.695965
2019-12-03    0.713702
2019-12-04    0.709032
2019-12-05    0.705225
Freq: D, Name: auc, dtype: float64

In [11]:
x.to_frame().reset_index().head()

hour       auc
0  2019-12-01  0.526705
1  2019-12-02  0.695965
2  2019-12-03  0.713702
3  2019-12-04  0.709032
4  2019-12-05  0.705225

In [12]:
abids = [456,15,16]

In [13]:
import plotly.express as px
px.line(df_on_tuwen[df_on_tuwen.abtest.isin(abids)], x='hour', y='auc', color='abtest')

In [14]:
abids2 = [456, 45600, 16, 1500, 1600]
px.line(df_tuwen[df_tuwen.abtest.isin(abids2)], x='hour', y='group/auc', color='abtest')

In [15]:
px.line(df_tuwen[df_tuwen.abtest.isin(abids2)], x='hour', y='group/auc', color='abtest')

In [16]:
px.line(df_tuwen[df_tuwen.abtest.isin(abids2)], x='hour', y='group/click/time_auc', color='abtest')

In [17]:
px.line(df_video[df_video.abtest.isin(abids2)], x='hour', y='group/auc', color='abtest')

In [18]:
def show(df, metric='auc', abids=abids, offline=False):
  if 'off' in df.name:
    offline = True
  if offline:
    abids = [x * 100 for x in abids]
  fig = px.line()
  for abid in abids:
    df_ = df[df.abtest==abid]
    fig.add_scatter(x=df_.hour, y=gezi.smooth(df_[metric].values, 0.), mode='lines', name=abid)
  fig.update_layout(
      title=df.name + ':' + metric,
#       xaxis_title='hour',
#       yaxis_title=metric,
  )
  py.iplot(fig)

In [19]:
# show(df_on_tuwen)

In [20]:
# show(df_on_tuwen, 'group/auc')

In [21]:
# show(df_on_tuwen, 'click/time_auc')

In [22]:
# show(df_on_tuwen, 'group/click/time_auc')

In [23]:
# show(df_on_video)

In [24]:
# show(df_on_video, 'group/auc')

In [25]:
# show(df_on_video, 'click/time_auc')

In [26]:
# show(df_on_video, 'group/click/time_auc')

In [27]:
def compare(df, metric='auc', smoothing=0., abids=abids, offline=False):
    if isinstance(abids, str):
        abids = [int(x) for x in abids.split(',')]
    if 'off' in df.name:
        offline = True
    if offline:
        abids = [x * 100 for x in abids]

    df_ = df

    datas = []
    for abid in abids:
        df = df_[df_.abtest==abid]
        df = df.fillna(0.4)
        if not len(df):
            continue
        data = go.Scatter(
            x=df.hour,
            y=gezi.smooth(df[metric].values, smoothing),
            mode='lines',
            line_shape='spline',
            line_smoothing=1.,
            name=str(abid) 
        )

        datas.append(data)

    layout = go.Layout(xaxis=dict(type='date'), title=f'{df_.name}:{metric}', hovermode='x')
    fig = go.Figure(data=datas, layout=layout)
    py.iplot(fig)

In [28]:
compare(df_off_tuwen, 'group/auc')

In [29]:
compare(df_on_tuwen, 'group/auc')

In [30]:
compare(df_on_tuwen, 'group/click/time_auc')

In [31]:
compare(df_off_tuwen, 'group/auc')

In [32]:
compare(df_off_tuwen, 'auc')

In [33]:
df_off_tuwen[df_off_tuwen.abtest==45600].sort_values('hour', ascending=False)[['hour', 'click/time_auc']]

hour  click/time_auc
2344 2020-01-06 06:00:00        0.611942
2343 2020-01-06 05:00:00        0.628581
2342 2020-01-06 04:00:00        0.632185
2341 2020-01-06 03:00:00        0.619718
2340 2020-01-06 02:00:00        0.606674
...                  ...             ...
1507 2019-12-01 04:00:00             NaN
1506 2019-12-01 03:00:00             NaN
1505 2019-12-01 02:00:00             NaN
1504 2019-12-01 01:00:00             NaN
1503 2019-12-01 00:00:00             NaN

[842 rows x 2 columns]

In [34]:
compare(df_off_tuwen, 'click/time_auc')

In [35]:
compare(df_off_tuwen, 'group/click/time_auc')

In [36]:
compare(df_on_tuwen, 'group/click/time_auc')

In [37]:
from projects.common.monitor.taurus import Taurus
from projects.common.monitor.show import show

In [38]:
last_days = 50
abids = [15]
worker_days = Taurus()
worker_days.init(abids, last_days, 'daily')
dfs_days, diffs_days = worker_days.run()

def show_days(name, diffs=None):
  figs = show(dfs_days, name, worker_days.stats, abids, mark='daily', diffs=diffs)
  for fig in figs:
    py.iplot(fig)

sql_search:=========== SELECT * FROM feed_abtest_daily WHERE product = 'sgsapp' AND data_obj in ('recommend_ge6511_weight_mean_article','recommend_ge6511_weight_mean_video','recommend_ge6511_weight_mean_small_video','recommend_ge6511_weight_mean','ge6511_weight_mean','quality') AND abtest in (4,6,15,5) AND date BETWEEN  '20191104'  AND  '20200106' AND user_obj = 'total' AND os = 'total'
sql_rel:============== SELECT * FROM feed_relative WHERE product = 'sgsapp'  AND abtest in (4,6,15,5) AND date BETWEEN  '20191104'  AND  '20200106' AND user_obj = 'total' 
sql_search:=========== SELECT * FROM feed_abtest_daily WHERE product = 'sgsapp' AND data_obj in ('recommend_ge6511_weight_mean_article','recommend_ge6511_weight_mean_video','recommend_ge6511_weight_mean_small_video','recommend_ge6511_weight_mean','ge6511_weight_mean','quality') AND abtest in (4,6,15,5) AND date BETWEEN  '20191104'  AND  '2020010608' AND user_obj = 'total' AND os = 'total'
sql_rel:============== SELECT * FROM feed_rela

In [39]:
%%html
<style>
.output_wrapper, .output {
    height:auto !important;
    max-height:10000px;  /* your desired max-height here */
}
.output_scroll {
    box-shadow:none !important;
    webkit-box-shadow:none !important;
}
</style>

In [40]:
# show_days('tuwen')

In [41]:
dfs_days['tuwen']

id product  abtest     os user_obj  \
580    908048  sgsapp       5  total    total   
1336   908032  sgsapp      15  total    total   
958    908050  sgsapp       6  total    total   
202    908046  sgsapp       4  total    total   
581    926788  sgsapp       5  total    total   
...       ...     ...     ...    ...      ...   
1384  1281880  sgsapp      15  total    total   
1385  1286600  sgsapp      15  total    total   
251   1286614  sgsapp       4  total    total   
629   1286616  sgsapp       5  total    total   
1007  1286618  sgsapp       6  total    total   

                                  data_obj      dis  dis_user  refresh_times  \
580   recommend_ge6511_weight_mean_article  6030054    138574              0   
1336  recommend_ge6511_weight_mean_article  6034525    138883              0   
958   recommend_ge6511_weight_mean_article  6007854    136970              0   
202   recommend_ge6511_weight_mean_article  5969139    136507              0   
581   recommend_ge6511_weight_mean_article  5496706    128981              0   
...                                    ...      ...       ...            ...   
1384  recommend_ge6511_weight_mean_article  5935390    144697              0   
1385  recommend_ge6511_weight_mean_article  5997587    144211              0   
251   recommend_ge6511_weight_mean_article  5993817    142543              0   
629   recommend_ge6511_weight_mean_article  6009042    143586              0   
1007  recommend_ge6511_weight_mean_article  5940641    142543              0   

      real_dis  ...      date       ctr  real_ctr  read_ratio      dur1  \
580    2688164  ...  20191117  0.057568  0.129135    0.351025  2.702301   
1336   2686319  ...  20191117  0.057160  0.128404    0.348790  2.737730   
958    2681405  ...  20191117  0.057363  0.128525    0.351968  2.744341   
202    2664515  ...  20191117  0.057291  0.128346    0.349836  2.690390   
581    2437629  ...  20191118  0.053563  0.120782    0.346222  2.449303   
...        ...  ...       ...       ...       ...         ...       ...   
1384   2565152  ...  20200104  0.048714  0.112717    0.284691  2.757589   
1385   2578553  ...  20200105  0.047926  0.111473    0.285152  2.970604   
251    2583929  ...  20200105  0.047989  0.111317    0.287429  2.961217   
629    2573868  ...  20200105  0.048083  0.112256    0.284979  2.971747   
1007   2557177  ...  20200105  0.048069  0.111670    0.286770  2.979438   

           dur2  finish_ratio  read_files   doc_dur  refresh  
580    7.698304      0.483092    2.505066  1.078734      0.0  
1336   7.849222      0.476720    2.483623  1.102313      0.0  
958    7.797141      0.483043    2.516077  1.090722      0.0  
202    7.690443      0.478569    2.505220  1.073914      0.0  
581    7.074382      0.457153    2.282677  1.072996      0.0  
...         ...           ...         ...       ...      ...  
1384   9.686237      0.450686    1.998224  1.380020      0.0  
1385  10.417629      0.444122    1.993184  1.490381      0.0  
251   10.302426      0.446455    2.017882  1.467487      0.0  
629   10.427949      0.446016    2.012257  1.476822      0.0  
1007  10.389657      0.449297    2.003318  1.487251      0.0  

[200 rows x 33 columns]

In [42]:
fig = px.line()
df = df_on_tuwen
metric = 'group/click/time_auc'
metric = 'click/time_auc'
abid = 456
df_ = df[df.abtest==abid]
fig.add_scatter(x=df_.hour, y=gezi.smooth(df_[metric].values * 3, 0.8), mode='lines', name=metric)
df_ = dfs_days['tuwen']
df_.hour = pd.to_datetime(df_.date, format='%Y%m%d')
fig.add_scatter(x=df_.hour, y=gezi.smooth(df_.dur2.values / 5., 0.8), mode='lines', name='dur2')
py.iplot(fig)